In [9]:
!pip install pydub mutagen pytaglib

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 894.4/894.4 KB 3.8 MB/s eta 0:00:0000:0100:01


In [ ]:
from pydub import AudioSegment
from pydub.utils import mediainfo
import taglib
import os

def make_mono(in_file, out_file):
    sound = AudioSegment.from_wav(in_file)
    sound = sound.set_channels(1)
    tags = mediainfo(in_file).get('TAG', {})
    tags['TRACKNUMBER'] = tags['track']
    print(in_file)
    sound.export(out_file, format="wav")
    with taglib.File(out_file, save_on_exit=True) as song:
        song.tags = tags
    print(mediainfo(out_file))

for file in os.listdir('../seth/wavs'):
    make_mono("../seth/wavs/"+file, "../sethmono/wavs/"+file)

../seth/wavs/SK001-0001.wav
{'index': '0', 'codec_name': 'pcm_s16le', 'codec_long_name': 'PCM signed 16-bit little-endian', 'profile': 'unknown', 'codec_type': 'audio', 'codec_tag_string': '[1][0][0][0]', 'codec_tag': '0x0001', 'sample_fmt': 's16', 'sample_rate': '22050', 'channels': '1', 'channel_layout': 'unknown', 'bits_per_sample': '16', 'id': 'N/A', 'r_frame_rate': '0/0', 'avg_frame_rate': '0/0', 'time_base': '1/22050', 'start_pts': 'N/A', 'start_time': 'N/A', 'duration_ts': '169216', 'duration': '7.674195', 'bit_rate': '354171', 'max_bit_rate': 'N/A', 'bits_per_raw_sample': 'N/A', 'nb_frames': 'N/A', 'nb_read_frames': 'N/A', 'nb_read_packets': 'N/A', 'DISPOSITION': {'default': '0', 'dub': '0', 'original': '0', 'comment': '0', 'lyrics': '0', 'karaoke': '0', 'forced': '0', 'hearing_impaired': '0', 'visual_impaired': '0', 'clean_effects': '0', 'attached_pic': '0', 'timed_thumbnails': '0'}, 'filename': '../sethmono/wavs/SK001-0001.wav', 'nb_streams': '1', 'nb_programs': '0', 'format_

In [1]:
import os

# Trainer: Where the ✨️ happens.
# TrainingArgs: Defines the set of arguments of the Trainer.
from trainer import Trainer, TrainerArgs

# GlowTTSConfig: all model related values for training, validating and testing.
from TTS.tts.configs.vits_config import VitsConfig

# BaseDatasetConfig: defines name, formatter and path of the dataset.
from TTS.tts.configs.shared_configs import BaseDatasetConfig
from TTS.tts.datasets import load_tts_samples
from TTS.tts.models.vits import Vits
from TTS.tts.utils.text.tokenizer import TTSTokenizer
from TTS.utils.audio import AudioProcessor

# we use the same path as this script as our training folder.
output_path = os.path.dirname(os.path.abspath('../../TTS'))

# DEFINE DATASET CONFIG
# Set LJSpeech as our target dataset and define its path.
# You can also use a simple Dict to define the dataset and pass it to your custom formatter.
dataset_config = BaseDatasetConfig(
    formatter="ljspeech", meta_file_train="metadata.csv", path=os.path.join(output_path, "SethVoice/sethmono")
)

# INITIALIZE THE TRAINING CONFIGURATION
# Configure the model. Every config class inherits the BaseTTSConfig.
config = VitsConfig(
    datasets=[dataset_config],
)

# INITIALIZE THE AUDIO PROCESSOR
# Audio processor is used for feature extraction and audio I/O.
# It mainly serves to the dataloader and the training loggers.
ap = AudioProcessor.init_from_config(config)

# INITIALIZE THE TOKENIZER
# Tokenizer is used to convert text to sequences of token IDs.
# If characters are not defined in the config, default characters are passed to the config
tokenizer, config = TTSTokenizer.init_from_config(config)

# LOAD DATA SAMPLES
# Each sample is a list of ```[text, audio_file_path, speaker_name]```
# You can define your custom sample loader returning the list of samples.
# Or define your custom formatter and pass it to the `load_tts_samples`.
# Check `TTS.tts.datasets.load_tts_samples` for more details.
train_samples, eval_samples = load_tts_samples(
    dataset_config,
    eval_split=True,
    eval_split_max_size=config.eval_split_max_size,
    eval_split_size=config.eval_split_size,
)

# INITIALIZE THE MODEL
# Models take a config object and a speaker manager as input
# Config defines the details of the model like the number of layers, the size of the embedding, etc.
# Speaker manager is used by multi-speaker models.
model = Vits(config, ap, tokenizer, speaker_manager=None)

# INITIALIZE THE TRAINER
# Trainer provides a generic API to train all the 🐸TTS models with all its perks like mixed-precision training,
# distributed training, etc.
trainer = Trainer(
    TrainerArgs(), config, output_path, model=model, train_samples=train_samples, eval_samples=eval_samples
)

# AND... 3,2,1... 🚀
trainer.fit()

 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024
 | > Found 435 files in /root/tts-output/SethVoice/sethmono


 > Training Environment:
 | > Backend: Torch
 | > Mixed precision: False
 | > Precision: float32
 | > Current device: 0
 | > Num. of GPUs: 1
 | > Num. of CPUs: 24
 | > Num. of Torch Threads: 12
 | > Torch seed: 54321
 | > Torch CUDNN: True
 | > Torch CUDNN deterministic: False
 | > Torch CUDNN benchmark: False
 | > Torch TF32 MatMul: False
 > Start Tensorboard: tensorboard --logdir=output/run-July-27-2023_12+50AM-0000000

 > Model has 83046892 parameters

 > EPOCH: 0/1000
 --> output/run-July-27-2023_12+50AM-0000000




> DataLoader initialization
| > Tokenizer:
	| > add_blank: True
	| > use_eos_bos: False
	| > use_phonemes: False
| > Number of instances : 431



 > TRAINING (2023-07-27 00:50:20) 


 | > Preprocessing samples
 | > Max text length: 169
 | > Min text length: 21
 | > Avg text length: 97.48027842227378
 | 
 | > Max audio length: 222621.0
 | > Min audio length: 35994.0
 | > Avg audio length: 131499.33874709977
 | > Num. instances discarded samples: 0
 | > Batch group size: 0.
eight. The press yard.

 [!] Character '\n' not found in the vocabulary. Discarding it.


...


  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.0417017936706543 (+0.0)
     | > avg_loss_disc: 2.796450138092041 (+0.0)
     | > avg_loss_disc_real_0: 0.42661386728286743 (+0.0)
     | > avg_loss_disc_real_1: 0.17794393002986908 (+0.0)
     | > avg_loss_disc_real_2: 0.1354532688856125 (+0.0)
     | > avg_loss_disc_real_3: 0.17521530389785767 (+0.0)
     | > avg_loss_disc_real_4: 0.23180800676345825 (+0.0)
     | > avg_loss_disc_real_5: 0.21772636473178864 (+0.0)
     | > avg_loss_0: 2.796450138092041 (+0.0)
     | > avg_loss_gen: 1.909071922302246 (+0.0)
     | > avg_loss_kl: 3.986734390258789 (+0.0)
     | > avg_loss_feat: 5.044821262359619 (+0.0)
     | > avg_loss_mel: 24.397520065307617 (+0.0)
     | > avg_loss_duration: 1.8762290477752686 (+0.0)
     | > avg_loss_1: 37.214378356933594 (+0.0)


 > EPOCH: 998/1000
 --> output/run-July-27-2023_12+50AM-0000000

 > TRAINING (2023-07-27 07:07:17) 

   --> TIME: 2023-07-27 07:07:22 -- STEP: 3/14 -- GLOBAL_STEP: 13975
     | > loss_di

 | > Synthesizing test sentences.



  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.03293657302856445 (+0.0)
     | > avg_loss_disc: 2.6298000812530518 (+0.0)
     | > avg_loss_disc_real_0: 0.055739641189575195 (+0.0)
     | > avg_loss_disc_real_1: 0.19378311932086945 (+0.0)
     | > avg_loss_disc_real_2: 0.14521482586860657 (+0.0)
     | > avg_loss_disc_real_3: 0.20006826519966125 (+0.0)
     | > avg_loss_disc_real_4: 0.2735370993614197 (+0.0)
     | > avg_loss_disc_real_5: 0.2417299747467041 (+0.0)
     | > avg_loss_0: 2.6298000812530518 (+0.0)
     | > avg_loss_gen: 1.8200758695602417 (+0.0)
     | > avg_loss_kl: 4.2083282470703125 (+0.0)
     | > avg_loss_feat: 5.268579959869385 (+0.0)
     | > avg_loss_mel: 23.672725677490234 (+0.0)
     | > avg_loss_duration: 1.8698153495788574 (+0.0)
     | > avg_loss_1: 36.83952713012695 (+0.0)


 > EPOCH: 999/1000
 --> output/run-July-27-2023_12+50AM-0000000

 > TRAINING (2023-07-27 07:07:39) 

 > EVALUATION 


  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.0373656749725

 | > Synthesizing test sentences.



  --> EVAL PERFORMANCE
     | > avg_loader_time: 0.03736567497253418 (+0.0)
     | > avg_loss_disc: 2.6062989234924316 (+0.0)
     | > avg_loss_disc_real_0: 0.2505311369895935 (+0.0)
     | > avg_loss_disc_real_1: 0.2931688129901886 (+0.0)
     | > avg_loss_disc_real_2: 0.17190399765968323 (+0.0)
     | > avg_loss_disc_real_3: 0.13028259575366974 (+0.0)
     | > avg_loss_disc_real_4: 0.19129213690757751 (+0.0)
     | > avg_loss_disc_real_5: 0.2704940140247345 (+0.0)
     | > avg_loss_0: 2.6062989234924316 (+0.0)
     | > avg_loss_gen: 2.130206823348999 (+0.0)
     | > avg_loss_kl: 4.179049491882324 (+0.0)
     | > avg_loss_feat: 4.671621799468994 (+0.0)
     | > avg_loss_mel: 24.659433364868164 (+0.0)
     | > avg_loss_duration: 1.858756184577942 (+0.0)
     | > avg_loss_1: 37.49906921386719 (+0.0)



In [1]:
import os
os.path.exists('/root/tts-output/run-July-26-2023_12+16AM-0000000/config.json')

True

In [2]:
from TTS.api import Synthesizer

tts = Synthesizer(tts_checkpoint="../TTS/output/run-July-27-2023_12+50AM-0000000/best_model_4102.pth", tts_config_path="../TTS/output/run-July-27-2023_12+50AM-0000000/config.json")

#tts = TTS(model_name="/root/tts-output/run-July-26-2023_12+16AM-0000000/best_model_1908.pth", progress_bar=True, gpu=True)

 > Using model: vits
 > Setting up Audio Processor...
 | > sample_rate:22050
 | > resample:False
 | > num_mels:80
 | > log_func:np.log10
 | > min_level_db:0
 | > frame_shift_ms:None
 | > frame_length_ms:None
 | > ref_level_db:None
 | > fft_size:1024
 | > power:None
 | > preemphasis:0.0
 | > griffin_lim_iters:None
 | > signal_norm:None
 | > symmetric_norm:None
 | > mel_fmin:0
 | > mel_fmax:None
 | > pitch_fmin:None
 | > pitch_fmax:None
 | > spec_gain:20.0
 | > stft_pad_mode:reflect
 | > max_norm:1.0
 | > clip_norm:True
 | > do_trim_silence:False
 | > trim_db:60
 | > do_sound_norm:False
 | > do_amp_to_db_linear:True
 | > do_amp_to_db_mel:True
 | > do_rms_norm:False
 | > db_level:None
 | > stats_path:None
 | > base:10
 | > hop_length:256
 | > win_length:1024


In [5]:
outputs = tts.tts(text="I am getting married on Saturday.")
tts.save_wav(outputs, "output.wav")

 > Text splitted to sentences.
['I am getting married on Saturday.']
 > Processing time: 0.5208323001861572
 > Real-time factor: 0.17451301086653245
